In [253]:
import pandas as pd
import yfinance as yf
from datetime import datetime
from datetime import date,timedelta
import yfinance as yf
import plotly.graph_objects as go
import plotly.express as px
import matplotlib.pyplot as plt
from prophet import Prophet
from prophet.plot import plot_plotly, plot_components_plotly
import seaborn as sns
import pandas_ta as ta
import numpy as np
import json
from tkinter import *
from tkinter import messagebox, ttk, END
from matplotlib import dates

In [254]:
today = date.today()

d1 = today.strftime('%Y-%m-%d')
end_date = d1
d2 = date.today() - timedelta(days=365)
d2 = d2.strftime('%Y-%m-%d')
start_date = d2

In [255]:
from curl_cffi import requests
session = requests.Session(impersonate="chrome")
ticker = input('Write ticker: ')
stock_data = yf.download(ticker, start = start_date, end = end_date, progress=False, auto_adjust=False, session=session)
if isinstance(stock_data.columns, pd.MultiIndex):
    stock_data.columns = stock_data.columns.droplevel(1)
stock_data

Price          Adj Close         Close           High           Low  \
Date                                                                  
2025-02-04  97871.820312  97871.820312  101745.617188  96208.109375   
2025-02-05  96615.445312  96615.445312   99113.210938  96174.828125   
2025-02-06  96593.296875  96593.296875   99168.609375  95707.351562   
2025-02-07  96529.085938  96529.085938  100154.140625  95653.882812   
2025-02-08  96482.453125  96482.453125   96877.804688  95702.492188   
...                  ...           ...            ...           ...   
2026-01-30  84128.656250  84128.656250   84602.164062  81071.476562   
2026-01-31  78621.117188  78621.117188   84136.921875  75815.882812   
2026-02-01  76974.445312  76974.445312   79322.609375  75698.898438   
2026-02-02  78688.765625  78688.765625   79258.609375  74551.335938   
2026-02-03  75633.546875  75633.546875   79118.851562  72897.140625   

Price                Open       Volume  
Date                                    
2025-02-04  101398.718750  73002130211  
2025-02-05   97878.007812  49125911241  
2025-02-06   96610.640625  45302471947  
2025-02-07   96581.320312  55741290456  
2025-02-08   96533.257812  22447526395  
...                   ...          ...  
2026-01-30   84562.726562  72083816087  
2026-01-31   84126.500000  70479259159  
2026-02-01   78626.125000  53372509744  
2026-02-02   76968.875000  75140589684  
2026-02-03   78693.507812  68249110822  

[365 rows x 6 columns]

In [256]:
#RSI, Garman, ATR, MACD
stock_data['RSI'] = ta.rsi(close = stock_data["Adj Close"], length=14)

stock_data['Garman'] = ((np.log(stock_data['High'])- np.log(stock_data['Low']))**2)/2-(2*np.log(2)-1)*((np.log(stock_data['Adj Close']) -np.log(stock_data['Open']))**2)

def compute_atr(stock_data):
    atr = ta.atr(high=stock_data['High'], low=stock_data['Low'], close=stock_data['Close'], length=14)
    return atr.sub(atr.mean()).div(atr.std())
stock_data['ATR'] = compute_atr(stock_data)

def compute_macd(stock_data, short_period=12, long_period=26, signal_period=9):
    # Compute MACD, Signal Line, and Histogram using pandas_ta
    macd = ta.macd(
        close=stock_data['Close'], 
        fast=short_period, 
        slow=long_period, 
        signal=signal_period
    )
    
    # Assign the results to new columns in the DataFrame
    stock_data['MACD'] = macd['MACD_12_26_9']  # Default naming format
    stock_data['Signal'] = macd['MACDs_12_26_9']
    stock_data['MACD_Histogram'] = macd['MACDh_12_26_9']
    
    return stock_data

# Apply the function to compute MACD
stock_data = compute_macd(stock_data)

today = date.today() 
two_weeks = today - timedelta(days=14)

#Last 14 days
technical_analysis = stock_data.iloc[-14:]
technical_analysis

Price          Adj Close         Close          High           Low  \
Date                                                                 
2026-01-21  89376.960938  89376.960938  90430.406250  87231.570312   
2026-01-22  89462.453125  89462.453125  90258.960938  88438.445312   
2026-01-23  89503.875000  89503.875000  91100.250000  88486.359375   
2026-01-24  89110.734375  89110.734375  89811.609375  89044.289062   
2026-01-25  86572.218750  86572.218750  89193.148438  86003.710938   
2026-01-26  88267.140625  88267.140625  88743.070312  86429.289062   
2026-01-27  89102.570312  89102.570312  89427.125000  87228.921875   
2026-01-28  89184.570312  89184.570312  90439.289062  88721.460938   
2026-01-29  84561.585938  84561.585938  89200.781250  83250.601562   
2026-01-30  84128.656250  84128.656250  84602.164062  81071.476562   
2026-01-31  78621.117188  78621.117188  84136.921875  75815.882812   
2026-02-01  76974.445312  76974.445312  79322.609375  75698.898438   
2026-02-02  78688.765625  78688.765625  79258.609375  74551.335938   
2026-02-03  75633.546875  75633.546875  79118.851562  72897.140625   

Price               Open       Volume        RSI    Garman       ATR  \
Date                                                                   
2026-01-21  88326.507812  56330422434  43.222702  0.000595 -1.039938   
2026-01-22  89378.523438  35549685694  43.514186  0.000207 -1.109986   
2026-01-23  89462.046875  38997586037  43.665092  0.000424 -1.088792   
2026-01-24  89506.148438  14558687712  42.504436  0.000029 -1.269832   
2026-01-25  89104.765625  36124986722  35.873699  0.000342 -1.174659   
2026-01-26  86566.523438  45329286974  42.341350  0.000203 -1.181467   
2026-01-27  88257.476562  38744942267  45.271365  0.000275 -1.200351   
2026-01-28  89104.046875  39807419296  45.563768  0.000184 -1.270104   
2026-01-29  89169.851562  64653083162  34.403718  0.001295 -0.874821   
2026-01-30  84562.726562  72083816087  33.574375  0.000898 -0.770770   
2026-01-31  84126.500000  70479259159  25.238992  0.003653 -0.153445   
2026-02-01  78626.125000  53372509744  23.370784  0.000919 -0.090808   
2026-02-02  76968.875000  75140589684  29.242876  0.001686  0.085136   
2026-02-03  78693.507812  68249110822  25.493470  0.002746  0.413130   

Price              MACD       Signal  MACD_Histogram  
Date                                                  
2026-01-21   443.165938   930.257717     -487.091780  
2026-01-22   200.724447   784.351063     -583.626616  
2026-01-23    11.794261   629.839703     -618.045442  
2026-01-24  -167.724017   470.326959     -638.050976  
2026-01-25  -508.963527   274.468862     -783.432389  
2026-01-26  -635.308822    92.513325     -727.822147  
2026-01-27  -660.413351   -58.072010     -602.341341  
2026-01-28  -666.014753  -179.660559     -486.354194  
2026-01-29 -1031.598482  -350.048143     -681.550339  
2026-01-30 -1340.804074  -548.199330     -792.604745  
2026-01-31 -2007.127195  -839.984903    -1167.142292  
2026-02-01 -2637.660419 -1199.520006    -1438.140413  
2026-02-02 -2964.854227 -1552.586850    -1412.267377  
2026-02-03 -3431.136293 -1928.296739    -1502.839554

In [257]:
import plotly.graph_objects as go

# ----------------------------
# Indicators
# ----------------------------
stock_data["M10"] = stock_data["Close"].rolling(window=10).mean()
stock_data["M20"] = stock_data["Close"].rolling(window=20).mean()

stock_data["M40"] = stock_data["Close"].rolling(window=40).mean()
stock_data["M80"] = stock_data["Close"].rolling(window=80).mean()

stock_data["SD"] = stock_data["Close"].rolling(window=20).std()
stock_data["UB"] = stock_data["M20"] + 2 * stock_data["SD"]
stock_data["LB"] = stock_data["M20"] - 2 * stock_data["SD"]


fig = go.Figure()

# 0 Close (line)
fig.add_trace(go.Scatter(
    x=stock_data.index, y=stock_data["Close"],
    mode="lines", name="Close"
))

# 1 Candles
fig.add_trace(go.Candlestick(
    x=stock_data.index,
    open=stock_data["Open"],
    high=stock_data["High"],
    low=stock_data["Low"],
    close=stock_data["Close"],
    name="Candles"
))

# 2-3 MA 10/20
fig.add_trace(go.Scatter(x=stock_data.index, y=stock_data["M10"], mode="lines", name="M10"))
fig.add_trace(go.Scatter(x=stock_data.index, y=stock_data["M20"], mode="lines", name="M20"))

# 4-5 MA 40/80
fig.add_trace(go.Scatter(x=stock_data.index, y=stock_data["M40"], mode="lines", name="M40"))
fig.add_trace(go.Scatter(x=stock_data.index, y=stock_data["M80"], mode="lines", name="M80"))

# 6-8 Bollinger Bands
fig.add_trace(go.Scatter(
    x=stock_data.index, y=stock_data["UB"],
    mode="lines", name="Upper BB"
))
fig.add_trace(go.Scatter(
    x=stock_data.index, y=stock_data["LB"],
    mode="lines", name="Lower BB",
    fill="tonexty"  # fill between UB (previous trace) and LB
))
fig.add_trace(go.Scatter(
    x=stock_data.index, y=stock_data["M20"],
    mode="lines", name="Middle BB (M20)"
))

# ----------------------------
# Visibility presets (length MUST be 9)
# ----------------------------
PRICE_CANDLES = [False, True,  False, False, False, False, False, False, False]
PRICE_LINE    = [True,  False, False, False, False, False, False, False, False]

MA_10_20      = [True,  False, True,  True,  False, False, False, False, False]
MA_40_80      = [True,  False, False, False, True,  True,  False, False, False]

BB_VIEW       = [True,  False, False, True,  False, False, True,  True,  True]
# (BB_VIEW includes Close + M20 + UB/LB + Middle; you can tweak if you want)

# Default view
for t in fig.data:
    t.visible = False
fig.data[1].visible = True  # default = candles

# ----------------------------
# Layout + Buttons (positioned to avoid title conflict)
# ----------------------------
fig.update_layout(
    title=dict(text=f"{ticker} Price", x=0.01, y=0.97),  # keep title slightly lower
    xaxis_title="Date",
    yaxis_title="Price",
    plot_bgcolor="lightgrey",
    xaxis_rangeslider_visible=False,
    width=1050,
    height=650,
    margin=dict(t=110, r=30, l=60, b=50),  # extra top margin for buttons + title
    updatemenus=[
        dict(
            type="buttons",
            direction="right",
            x=1.0,
            y=1.16,
            xanchor="right",
            yanchor="top",
            pad={"r": 10, "t": 10},
            buttons=[
                dict(
                    label="Candles",
                    method="update",
                    args=[{"visible": PRICE_CANDLES},
                          {"title": f"{ticker} Price (Candles)", "yaxis": {"title": "Price"}}],
                ),
                dict(
                    label="Line",
                    method="update",
                    args=[{"visible": PRICE_LINE},
                          {"title": f"{ticker} Price (Line)", "yaxis": {"title": "Price"}}],
                ),
                dict(
                    label="MA 10/20",
                    method="update",
                    args=[{"visible": MA_10_20},
                          {"title": f"{ticker} Moving Averages (10/20)", "yaxis": {"title": "Price"}}],
                ),
                dict(
                    label="MA 40/80",
                    method="update",
                    args=[{"visible": MA_40_80},
                          {"title": f"{ticker} Moving Averages (40/80)", "yaxis": {"title": "Price"}}],
                ),
                dict(
                    label="Bollinger",
                    method="update",
                    args=[{"visible": BB_VIEW},
                          {"title": f"{ticker} Bollinger Bands (20, 2σ)", "yaxis": {"title": "Price"}}],
                ),
            ],
        )
    ],
)

fig.show()


Sharpe and Sortino Ratio

In [258]:
stock_data = stock_data.copy()
stock_data["Daily Returns"] = stock_data["Adj Close"].pct_change()
stock_data.dropna(inplace=True)

def compute_sharpe_ratio(data, risk_free_rate=0, periods=365):
    """
    Computes daily and annualized Sharpe Ratio
    """
    returns = data["Daily Returns"]
    excess_returns = returns - risk_free_rate / periods

    daily_sharpe = excess_returns.mean() / returns.std()
    annual_sharpe = daily_sharpe * np.sqrt(periods)

    return daily_sharpe, annual_sharpe

def compute_sortino_ratio(data, threshold=0, risk_free_rate=0, periods=365):
    """
    Computes annualized Sortino Ratio
    """
    returns = data["Daily Returns"]
    downside_returns = returns[returns < threshold]

    downside_std = downside_returns.std()
    excess_return = returns.mean() - risk_free_rate / periods

    sortino = (excess_return / downside_std) * np.sqrt(periods)
    return sortino


daily_sharpe, annual_sharpe = compute_sharpe_ratio(stock_data)
sortino = compute_sortino_ratio(stock_data)

print(f"Daily Sharpe Ratio for {ticker}: {daily_sharpe:.4f}")
print(f"Annual Sharpe Ratio for {ticker}: {annual_sharpe:.4f}")
print(f"Sortino Ratio for {ticker}: {sortino:.4f}")


Daily Sharpe Ratio for BTC-USD: -0.0299
Annual Sharpe Ratio for BTC-USD: -0.5721
Sortino Ratio for BTC-USD: -0.7941


In [259]:
prices = pd.concat([xrp, btc, eth], axis=1)
prices.columns = ["XRP", "BTC", "ETH"]
prices = prices.dropna()

# daily log returns
log_returns = np.log(prices / prices.shift(1)).dropna()

def monte_carlo_paths(price_series, mu, sigma, days=365, n_sims=5000, seed=42):
    """
    Geometric Brownian Motion (GBM) simulation using log returns
    """
    rng = np.random.default_rng(seed)
    s0 = float(price_series.iloc[-1])

    # random daily shocks
    z = rng.standard_normal((days, n_sims))

    # GBM in log space: S(t) = S0 * exp( (mu - 0.5*sigma^2)*t + sigma*W )
    drift = (mu - 0.5 * sigma**2)
    daily_log_steps = drift + sigma * z
    log_paths = np.cumsum(daily_log_steps, axis=0)
    paths = s0 * np.exp(log_paths)

    # add S0 as day 0
    paths = np.vstack([np.full((1, n_sims), s0), paths])
    return paths  # shape: (days+1, n_sims)

def summarize_paths(paths):
    terminal = paths[-1, :]
    s0 = paths[0, 0]
    summary = {
        "Start": s0,
        "Mean End": terminal.mean(),
        "Median End": np.median(terminal),
        "P05 End": np.percentile(terminal, 5),
        "P95 End": np.percentile(terminal, 95),
        "Prob End > Start": (terminal > s0).mean()
    }
    return summary, terminal

DAYS = 365
N_SIMS = 50000

results = {}
terminals = {}

for coin in ["XRP", "BTC", "ETH"]:
    mu = log_returns[coin].mean()
    sigma = log_returns[coin].std()

    paths = monte_carlo_paths(prices[coin], mu, sigma, days=DAYS, n_sims=N_SIMS, seed=42)
    summary, terminal = summarize_paths(paths)

    results[coin] = summary
    terminals[coin] = terminal

# Print results
for coin, s in results.items():
    print(f"\n--- {coin} Monte Carlo ({DAYS} days, {N_SIMS} sims) ---")
    print(f"Start:            {s['Start']:.6f}")
    print(f"Mean End:         {s['Mean End']:.6f}")
    print(f"Median End:       {s['Median End']:.6f}")
    print(f"5th % End:        {s['P05 End']:.6f}")
    print(f"95th % End:       {s['P95 End']:.6f}")
    print(f"Prob End > Start: {s['Prob End > Start']*100:.2f}%")


coin_list = ["XRP", "BTC", "ETH"]

PLOT_SIMS = 200
plot_paths = {}

for coin in coin_list:
    mu = log_returns[coin].mean()
    sigma = log_returns[coin].std()
    plot_paths[coin] = monte_carlo_paths(prices[coin], mu, sigma, days=DAYS, n_sims=PLOT_SIMS, seed=7)

fig = go.Figure()

trace_groups = {}

for i, coin in enumerate(coin_list):
    paths = plot_paths[coin]
    trace_idxs = []

    # spaghetti paths
    for s in range(paths.shape[1]):
        fig.add_trace(go.Scatter(
            x=np.arange(paths.shape[0]),
            y=paths[:, s],
            mode="lines",
            name=f"{coin} sim",
            line=dict(width=1),
            opacity=0.15,
            showlegend=False,
            visible=(i == 0)
        ))
        trace_idxs.append(len(fig.data) - 1)

    # mean path
    fig.add_trace(go.Scatter(
        x=np.arange(paths.shape[0]),
        y=paths.mean(axis=1),
        mode="lines",
        name=f"{coin} mean",
        line=dict(width=3),
        visible=(i == 0)
    ))
    trace_idxs.append(len(fig.data) - 1)

    trace_groups[coin] = trace_idxs

buttons = []
for coin in coin_list:
    visible = [False] * len(fig.data)
    for idx in trace_groups[coin]:
        visible[idx] = True

    buttons.append(dict(
        label=coin,
        method="update",
        args=[
            {"visible": visible},
            {"title": f"{coin} Monte Carlo Paths ({DAYS} days, {PLOT_SIMS} sims shown)",
             "xaxis": {"title": "Day"},
             "yaxis": {"title": "Simulated Price"}}
        ],
    ))

fig.update_layout(
    title=f"XRP Monte Carlo Paths ({DAYS} days, {PLOT_SIMS} sims shown)",
    width=1050,
    height=600,
    plot_bgcolor="lightgrey",
    updatemenus=[dict(
        type="buttons",
        direction="right",
        x=1.0,
        y=1.15,
        xanchor="right",
        yanchor="top",
        pad={"r": 10, "t": 10},
        buttons=buttons
    )],
    margin=dict(t=110, r=30, l=60, b=50)
)

fig.show()

fig2 = go.Figure()

hist_groups = {}
for i, coin in enumerate(coin_list):
    terminal = terminals[coin]
    fig2.add_trace(go.Histogram(
        x=terminal,
        nbinsx=60,
        name=f"{coin} terminal",
        opacity=0.75,
        visible=(i == 0)
    ))
    hist_groups[coin] = len(fig2.data) - 1

buttons2 = []
for coin in coin_list:
    visible = [False] * len(fig2.data)
    visible[hist_groups[coin]] = True

    s = results[coin]
    subtitle = (f"Start={s['Start']:.6f} | Mean={s['Mean End']:.6f} | "
                f"P05={s['P05 End']:.6f} | P95={s['P95 End']:.6f} | "
                f"P(End>Start)={s['Prob End > Start']*100:.2f}%")

    buttons2.append(dict(
        label=coin,
        method="update",
        args=[
            {"visible": visible},
            {"title": f"{coin} Terminal Price Distribution<br><sup>{subtitle}</sup>",
             "xaxis": {"title": "Terminal Price"},
             "yaxis": {"title": "Count"}}
        ],
    ))

fig2.update_layout(
    title="XRP Terminal Price Distribution",
    width=1050,
    height=600,
    plot_bgcolor="lightgrey",
    updatemenus=[dict(
        type="buttons",
        direction="right",
        x=1.0,
        y=1.15,
        xanchor="right",
        yanchor="top",
        pad={"r": 10, "t": 10},
        buttons=buttons2
    )],
    margin=dict(t=110, r=30, l=60, b=50)
)

fig2.show()



--- XRP Monte Carlo (365 days, 50000 sims) ---
Start:            1.574199
Mean End:         0.972423
Median End:       0.713107
5th % End:        0.193780
95th % End:       2.624976
Prob End > Start: 15.66%

--- BTC Monte Carlo (365 days, 50000 sims) ---
Start:            75633.546875
Mean End:         58317.591485
Median End:       53490.856171
5th % End:        26875.277253
95th % End:       106480.917980
Prob End > Start: 20.19%

--- ETH Monte Carlo (365 days, 50000 sims) ---
Start:            2227.558838
Mean End:         1806.915963
Median End:       1367.421523
5th % End:        397.660010
95th % End:       4703.386731
Prob End > Start: 25.65%
